In [5]:
%matplotlib inline
import json
import folium
import pandas as pd
from src import utils
from bike import Bike
from folium.plugins import TimestampedGeoJson

with open("data/stations_loc.json") as f:
    stations = json.load(f)

key = open("data/cycle_street_key.txt", "r").read()

# {3907, 1605, 1863, 3278, 4879, 17, 4853, 791, 540, 893}
data = pd.read_pickle("data/top_ten_bikes.pickle")

data['check_stations_ids'] = data.apply(lambda row: utils.check_id(row,stations), axis=1)
data = data[data['check_stations_ids']==True]

#bike_id = 893
#data =data[(data['start_date']> '2020-04-01') & (data['start_date']< '2020-05-01')]

bike_id = 17
data =data[(data['start_date']> '2014-07-01') & (data['start_date']< '2014-08-01')]

bike = Bike(id=bike_id)
bike.get_story(data, stations)
bike.visualize_routes(key)
traj = utils.get_trajectory(bike_id)

In [7]:
features = utils.traj_to_timestamped_geojson(traj)
xy = traj.get_start_location()
# Create base map
London = [51.506949, -0.122876]
map = folium.Map(location=London, zoom_start=12, tiles="cartodbpositron")
TimestampedGeoJson(
    {
        "type": "FeatureCollection",
        "features": features,
    },
    period="PT1S",
    add_last_point=False,
    transition_time=10
).add_to(map)

map